# Moving averages in SQL

In [ ]:
from pandas import DataFrame
import matplotlib.pyplot as plt
from data201 import db_connection, df_query

%matplotlib inline

In [ ]:
conn = db_connection(config_file='stock-prices.ini')
cursor = conn.cursor()

In [ ]:
table = cursor.execute('SELECT * FROM recent_prices')
table = cursor.fetchall()
table

In [ ]:
def compute_moving_averages(cursor, n):
    """
    @cursor the database cursor
    @n the number of days to average
    """
    cursor.execute(
       f"""
        SELECT days_ago, price,
            IF ( ROW_NUMBER() OVER (ORDER BY days_ago) >= {n},
                 AVG(price) OVER (ORDER BY days_ago
                                  ROWS BETWEEN {n - 1} PRECEDING
                                  AND CURRENT ROW),
                 NULL
            )
        FROM recent_prices
        ORDER BY days_ago
        """
    )
    
    return cursor.fetchall()

In [ ]:
table = []
columns = ['days ago', 'price']
first = True

for days in [3, 5, 10]:
    graph_label = f'{days}_day_moving_average'
    columns += [graph_label,]
    
    print()
    print(graph_label)
    print()

    averages = compute_moving_averages(cursor, days)
    display(averages)

    if first:
        table = averages.copy()
        first = False
    else:
        for i in range(len(averages)):
            table[i] += (averages[i][2],)

In [ ]:
df = DataFrame(table)
df.columns = columns
df

In [ ]:
rows = df.values.tolist()
xs   = [row[0] for row in rows]
ys   = [row[1] for row in rows]

plt.figure(figsize=(15, 10))

# Initialize the graph and plot the prices.
plt.xticks(xs)
plt.plot(xs, ys, linewidth=5)
plt.title('Moving Average of Stock Prices')
plt.xlabel('Days ago')
plt.ylabel('Price')

days_ago = [3, 5, 10]

for i in range(len(days_ago)):
    days = days_ago[i]
    graph_label = f'{days}_day_moving_average'

    xs   = [row[0] for row in rows]
    ys   = [row[1] for row in rows]
    avgs = [row[i + 2] for row in rows]
    
    # Plot the moving average line.
    plt.plot(xs[days - 1:], avgs[days - 1:], label=graph_label)
    
plt.legend()
plt.show()

In [ ]:
conn.close()